# Окэй летсгоу

In [66]:
!pip install catboost

In [427]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

from catboost import CatBoostClassifier, Pool

%matplotlib inline

In [429]:
df = pd.read_csv("./startup_train.csv")

In [431]:
df

index                name  \
0         0         Stackdriver   
1         1  Authix Tecnologies   
2         2              Lytics   
3         3       1World Online   
4         4      Enure Networks   
...     ...                 ...   
5507   5507                 ice   
5508   5508         Course Hero   
5509   5509        DVS Sciences   
5510   5510               KAYAK   
5511   5511           Procam TV   

                                               overview  category_code  \
0     Stackdriver provides a [powerfully simple moni...     enterprise   
1     Authix Tecnologies is a Torino based start-up ...       security   
2     Lytics provides B2C marketers the first analyt...       software   
3     1World Online is a Silicon Valley-based startu...     enterprise   
4     Enure Networks, Ltd. provides home-network man...       software   
...                                                 ...            ...   
5507  Ice.com is one of the leading e-commerce websi...      ecommerce   
5508  Course Hero is a digital learning platform tha...      education   
5509  DVS Sciences, Inc. manufactures and has global...  manufacturing   
5510  KAYAK is a travel search engine.  It indexes h...         search   
5511  Procam Television has been supplying kit and c...    games_video   

                                               tag_list country_code  \
0     application-management, cloud-monitoring, moni...          USA   
1                               authentication-solution          GRC   
2            analytics, big-data, data-science, bigdata          USA   
3          social-research, big-data, analytics, mobile          USA   
4                                                   NaN          ISR   
...                                                 ...          ...   
5507                                 jewelry, ecommerce          USA   
5508  social-learning-network, online-courses, onlin...          USA   
5509                                                NaN          USA   
5510                      travel, travelsearch, airfare          USA   
5511                                                NaN          GBR   

      num_prev_rounds  has_raised_amount  ln_raised_amount  participants  \
0                   1                  1         15.424948             1   
1                   1                  1         13.340052             1   
2                   2                  1         14.603968             5   
3                   1                  1         13.815511             1   
4                   1                  1         15.894952             2   
...               ...                ...               ...           ...   
5507                1                  1         17.665658             1   
5508                2                  1         14.220976             6   
5509                1                  1         16.496532             3   
5510                1                  1         15.955577             2   
5511                1                  1         14.818879             0   

      previous_any_founder_experience  ipo_prob   ma_prob  has_next_round  
0                                   0  0.024390  0.182927               1  
1                                   0  0.000000  0.000000               1  
2                                   0  0.021505  0.242105               0  
3                                   0  0.000000  0.000000               0  
4                                   0  0.000000  0.000000               1  
...                               ...       ...       ...             ...  
5507                                0  0.000000  0.013889               0  
5508                                0  0.010811  0.128342               0  
5509                                0  0.000000  0.106667               0  
5510                                0  0.333333  0.000000               1  
5511                                0  0.000000  0.000000               0  

[5512

# Создание столбцов с категориями

In [ ]:
df["tag_list"] = df["tag_list"].fillna("") 

In [243]:
tag_lists = df['tag_list'].str.split(',')

In [245]:
all_tags = set(map(str.strip, [item for sublist in tag_lists for item in sublist])) - set([""])

In [257]:
len(all_tags), all_tags

(9343,
 {'mythology',
  'comedy',
  'collect',
  'mobile-broadband',
  'server-load-balancer',
  'agile',
  'ticket-reseller',
  'network-latency',
  'cem',
  'web-conference',
  'carpool',
  'news-tracker',
  'job-hunting',
  'interests',
  'localized-video',
  'passbook-pass-designer',
  'notetaking',
  'hotel-reservations',
  'banner-ads',
  'digital-education',
  'venture-capital-data',
  'customer-analytics',
  'tours',
  'behavior-modification',
  'crowd-sourced-information',
  'lendingclub',
  'in-touch-weekly',
  'adaptive',
  'output-management',
  'switzerland',
  'smart-travel',
  'electronic-health-records',
  'aircraft-maintenance',
  'free-av',
  'lighting',
  'web-application-acceleration',
  'baby-clothes',
  'grocery-list',
  'hedge-fund',
  'safety-management-software',
  'moble-backhaul',
  'online-video-education',
  'invisible-web',
  'patented',
  'nlp',
  'medical-home',
  'social-learning-network',
  'port-access-control',
  'online-lms',
  'eyewitness-news',
  

In [249]:
for tag in all_tags:
    df[f'has_{tag.replace("-", "_").replace(" ", "_")}_tag'] = df['tag_list'].apply(lambda x: 1 if tag in x else 0)


C:\Users\webri\AppData\Local\Temp\ipykernel_5188\2976826100.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'has_{tag.replace("-", "_").replace(" ", "_")}_tag'] = df['tag_list'].apply(lambda x: 1 if tag in x else 0)
C:\Users\webri\AppData\Local\Temp\ipykernel_5188\2976826100.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'has_{tag.replace("-", "_").replace(" ", "_")}_tag'] = df['tag_list'].apply(lambda x: 1 if tag in x else 0)
C:\Users\webri\AppData\Local\Temp\ipykernel_5188\2976826100.py:2: PerformanceWarning: 

In [261]:
df.sum(numeric_only=True).round(2)

index                   15188316.00
num_prev_rounds             7742.00
has_raised_amount           5045.00
ln_raised_amount           75950.85
participants               11696.00
                           ...     
has_appconomy_tag              1.00
has_online_games_tag          12.00
has_pt_software_tag            1.00
has_solarpanels_tag            1.00
has_hosted_bi_tag              1.00
Length: 9352, dtype: float64

#### Кажется тэги проще выкинуть)))

# Обучаем модельку ЧПЕК

In [434]:
features = df.drop(columns=["index", "name", "overview", "has_next_round", "tag_list"])
result = df["has_next_round"]
features

category_code country_code  num_prev_rounds  has_raised_amount  \
0        enterprise          USA                1                  1   
1          security          GRC                1                  1   
2          software          USA                2                  1   
3        enterprise          USA                1                  1   
4          software          ISR                1                  1   
...             ...          ...              ...                ...   
5507      ecommerce          USA                1                  1   
5508      education          USA                2                  1   
5509  manufacturing          USA                1                  1   
5510         search          USA                1                  1   
5511    games_video          GBR                1                  1   

      ln_raised_amount  participants  previous_any_founder_experience  \
0            15.424948             1                                0   
1            13.340052             1                                0   
2            14.603968             5                                0   
3            13.815511             1                                0   
4            15.894952             2                                0   
...                ...           ...                              ...   
5507         17.665658             1                                0   
5508         14.220976             6                                0   
5509         16.496532             3                                0   
5510         15.955577             2                                0   
5511         14.818879             0                                0   

      ipo_prob   ma_prob  
0     0.024390  0.182927  
1     0.000000  0.000000  
2     0.021505  0.242105  
3     0.000000  0.000000  
4     0.000000  0.000000  
...        ...       ...  
5507  0.000000  0.013889  
5508  0.010811  0.128342  
5509  0.000000  0.106667  
5510  0.333333  0.000000  
5511  0.000000  0.000000  

[5512 rows x 9 columns]

In [436]:
cat_features_names = ["category_code", "country_code", "has_raised_amount", "previous_any_founder_experience"]

In [440]:
model = CatBoostClassifier(iterations=1000)

In [442]:
model.fit(features, result, cat_features_names)

Learning rate set to 0.021354
0:	learn: 0.6910928	total: 15.4ms	remaining: 15.4s
1:	learn: 0.6893611	total: 28.9ms	remaining: 14.4s
2:	learn: 0.6878245	total: 42ms	remaining: 14s
3:	learn: 0.6863983	total: 55ms	remaining: 13.7s
4:	learn: 0.6849609	total: 66.6ms	remaining: 13.2s
5:	learn: 0.6836283	total: 77.8ms	remaining: 12.9s
6:	learn: 0.6822172	total: 88.4ms	remaining: 12.5s
7:	learn: 0.6808235	total: 99.6ms	remaining: 12.3s
8:	learn: 0.6794064	total: 111ms	remaining: 12.2s
9:	learn: 0.6777194	total: 122ms	remaining: 12.1s
10:	learn: 0.6765586	total: 131ms	remaining: 11.8s
11:	learn: 0.6753416	total: 140ms	remaining: 11.5s
12:	learn: 0.6744874	total: 151ms	remaining: 11.5s
13:	learn: 0.6734225	total: 162ms	remaining: 11.4s
14:	learn: 0.6724586	total: 174ms	remaining: 11.4s
15:	learn: 0.6717507	total: 185ms	remaining: 11.4s
16:	learn: 0.6708198	total: 196ms	remaining: 11.3s
17:	learn: 0.6700197	total: 208ms	remaining: 11.4s
18:	learn: 0.6689536	total: 224ms	remaining: 11.6s
19:	learn

# Тестирование малыша

In [444]:
test_df = pd.read_csv("startup_test.csv")

In [446]:
test_df

index                             name  \
0      5512                   AudiSoft Group   
1      5513                           Trefis   
2      5514  Restore Medical Solutions, Inc.   
3      5515                     IMedExchange   
4      5516                        Markafoni   
...     ...                              ...   
1373   6885                          Petpace   
1374   6886                           eSpark   
1375   6887                        InVision.   
1376   6888                           Exelis   
1377   6889                          Stipple   

                                               overview     category_code  \
0     AudiSoft Group SAS, through its subsidiaries o...         messaging   
1     Trefis is a stock analysis service that breaks...         analytics   
2     Restore Medical Solutions, Inc. is a Corporati...           medical   
3     iMedExchange is connecting physicians around t...               web   
4     Markafoni is the first and leading Turkish Pri...         ecommerce   
...                                                 ...               ...   
1373  PetPace and its innovative pet monitoring appl...              pets   
1374  eSpark is pandora for education.\\r\nInnovativ...         education   
1375  InVision allows designers to build fully-inter...  public_relations   
1376  They are a leader in delivering mission-critic...          software   
1377  Stipple revolutionizes image monetization & so...       advertising   

                                               tag_list country_code  \
0                                                   NaN          FRA   
1     stock, stock-analysis, product-analysis, dcf, ...          USA   
2     healthcare, innovation, hospitals, surgery-cen...          USA   
3                                                   NaN          USA   
4     fashion, turkey, shopping, club, private, life...          TUR   
...                                                 ...          ...   
1373                                                NaN          USA   
1374                                          education          USA   
1375  web-applications, ux, ui, prototypes, prototyp...          USA   
1376                                                NaN          USA   
1377              photo, annotation, labels, e-commerce          USA   

      num_prev_rounds  has_raised_amount  ln_raised_amount  participants  \
0                   1                  1         15.525698             2   
1                   2                  1         14.285514             0   
2                   1                  1         14.751604             2   
3                   1                  1         14.731801             0   
4                   1                  1         15.830414             0   
...               ...                ...               ...           ...   
1373                1                  0          0.000000             1   
1374                1                  1         15.555977             4   
1375                1                  1         14.220976             1   
1376                1                  1         14.508658             1   
1377                1                  1         14.508658            11   

      previous_any_founder_experience  ipo_prob   ma_prob  
0                                   0  0.000000  0.111111  
1                                   0  0.000000  0.000000  
2                                   0  0.000000  0.000000  
3                                   0  0.000000  0.000000  
4                                   0  0.000000  0.000000  
...                               ...       ...       ...  
1373                                1  0.000000  0.000000  
1374                                0  0.000000  0.096774  
1375                                1  0.000000  0.017544  
1376                                0  0.000000  0.000000  
1377                                0  0.008876  0.112426  

[1378

In [448]:
test_features = test_df.drop(columns=["index", "name", "overview", "tag_list"])

In [450]:
test_df

index                             name  \
0      5512                   AudiSoft Group   
1      5513                           Trefis   
2      5514  Restore Medical Solutions, Inc.   
3      5515                     IMedExchange   
4      5516                        Markafoni   
...     ...                              ...   
1373   6885                          Petpace   
1374   6886                           eSpark   
1375   6887                        InVision.   
1376   6888                           Exelis   
1377   6889                          Stipple   

                                               overview     category_code  \
0     AudiSoft Group SAS, through its subsidiaries o...         messaging   
1     Trefis is a stock analysis service that breaks...         analytics   
2     Restore Medical Solutions, Inc. is a Corporati...           medical   
3     iMedExchange is connecting physicians around t...               web   
4     Markafoni is the first and leading Turkish Pri...         ecommerce   
...                                                 ...               ...   
1373  PetPace and its innovative pet monitoring appl...              pets   
1374  eSpark is pandora for education.\\r\nInnovativ...         education   
1375  InVision allows designers to build fully-inter...  public_relations   
1376  They are a leader in delivering mission-critic...          software   
1377  Stipple revolutionizes image monetization & so...       advertising   

                                               tag_list country_code  \
0                                                   NaN          FRA   
1     stock, stock-analysis, product-analysis, dcf, ...          USA   
2     healthcare, innovation, hospitals, surgery-cen...          USA   
3                                                   NaN          USA   
4     fashion, turkey, shopping, club, private, life...          TUR   
...                                                 ...          ...   
1373                                                NaN          USA   
1374                                          education          USA   
1375  web-applications, ux, ui, prototypes, prototyp...          USA   
1376                                                NaN          USA   
1377              photo, annotation, labels, e-commerce          USA   

      num_prev_rounds  has_raised_amount  ln_raised_amount  participants  \
0                   1                  1         15.525698             2   
1                   2                  1         14.285514             0   
2                   1                  1         14.751604             2   
3                   1                  1         14.731801             0   
4                   1                  1         15.830414             0   
...               ...                ...               ...           ...   
1373                1                  0          0.000000             1   
1374                1                  1         15.555977             4   
1375                1                  1         14.220976             1   
1376                1                  1         14.508658             1   
1377                1                  1         14.508658            11   

      previous_any_founder_experience  ipo_prob   ma_prob  
0                                   0  0.000000  0.111111  
1                                   0  0.000000  0.000000  
2                                   0  0.000000  0.000000  
3                                   0  0.000000  0.000000  
4                                   0  0.000000  0.000000  
...                               ...       ...       ...  
1373                                1  0.000000  0.000000  
1374                                0  0.000000  0.096774  
1375                                1  0.000000  0.017544  
1376                                0  0.000000  0.000000  
1377                                0  0.008876  0.112426  

[1378

In [452]:
predictions = model.predict(test_features)

In [454]:
result_df = test_df[["index"]].copy(deep=True)

In [456]:
result_df["has_next_round"] = predictions

In [460]:
result_df.to_csv("my_result.csv", index=False)